# Vector Auto Regression Model - Team Gannett Peak

### Team Members: Congda Xu, Binqi Shen,  Matthew Ko, Isaac Choi

#### import packages

In [10]:
import pandas as pd
import numpy as np
from datetime import timedelta
from dateutil.relativedelta import relativedelta
from datetime import datetime
from dateutil.parser import parse
from statsmodels.tsa.vector_ar.var_model import VAR
import warnings
warnings.filterwarnings('ignore')

In [3]:
def load_data(file):
    # initialize an empty list to store info of each company
    result = []  
    data = pd.read_csv(file)
    data = data.drop(['Cbsa_Pop_Percentile(20s)_min', 'Cbsa_Pop_Percentile(20s)_max'], axis='columns')
    
    # remove any null/infinite rows
    data = data[~data.isin([np.nan, np.inf, -np.inf]).any(1)] 
    
    # each group has full information of a unique company ticker 
    grouped = data.groupby(['Ticker'])         
    l_grouped = list(grouped)        
    
    for item in l_grouped:   
        df = item[1]
        # Due to 2-month lagging: the job-related data on '2019-11-01' corresponds to stock-related data on '2020-01-01'
        df = df[df['Date'] <= '2019-11-01']   
        df['Date'] = pd.to_datetime(df.Date , format = '%Y-%m')  # store all Date info in monthly interval
        df = df.set_index(['Date'])
        result.append(df)
        
    return result   # return a list of dataframes where each dataframe contains info of one company's monthly data

In [4]:
def find_constant(df):
    for column in df.columns:
        if len(df[column].unique()) == 1:
            return True
    return False

### Load in dataset (lagging period = 2)

In [5]:
# load the 2-month lagging data
dfs = load_data('final_data_2.csv')

In [6]:
dfs  # a list of dataframes

[           Ticker  New_Cbsa        Salary  average_posting_duration  \
 Date                                                                  
 2016-06-01      A         4  55166.666667                  7.000000   
 2016-08-01      A        16  88190.476190                 11.307692   
 2016-09-01      A         2  85694.444444                 22.368421   
 2016-10-01      A         6  92482.758621                 17.451613   
 2016-11-01      A         6  84805.555556                 19.303797   
 2016-12-01      A         2  83320.000000                 25.151515   
 2017-01-01      A         0  84397.058824                 29.762712   
 2017-02-01      A         2  87805.555556                 25.468354   
 2017-03-01      A         1  85785.714286                 20.592000   
 2017-04-01      A         0  74810.344828                 30.946809   
 2017-05-01      A         0  84187.500000                 54.115385   
 2017-06-01      A         2  74581.081081                 11.20

### Sample code: use '2019-05-01' predict '2019-06-01'

In [13]:
idx = []           # initialize a list to store index 
predictions = []   # initialize a list to store predicted stock prices

for i in range(len(dfs)):
    # remove ticker since it's non-numeric & can't be used in the model
    df_i = dfs[i].drop(['Ticker'], axis='columns')  
    
    if not find_constant(df_i) \
    and len(df_i) >= 12 \
    and df_i['Adj Close'].mean() < 5000 \
    and str(df_i.index[-6]) == '2019-06-01 00:00:00':
        idx.append(i)               # store index to match ticker later
        train_i = df_i[:-6]         # training dataset: all data until '2019-05-01'
        
        model = VAR(endog=train_i)  # train VAR model with the training dataset
        model_fit = model.fit()
        prediction = model_fit.forecast(model_fit.y, steps=1)  # steps=1: forecast next month '2019-06-01'
        predictions.append(prediction[0]) # add to the list that stores predictions
        
# print(len(predictions))           # original: 1769 ; after filter (6th till last: '2019-06-01'): 1364
print(predictions)

[array([-1.33180610e-01,  9.02889971e+04,  3.81725999e+01,  1.22626647e+02,
        7.54777501e+01,  2.06099410e-01,  2.39026594e+00,  7.11662213e+01]), array([1.47527475e-01, 6.23078457e+04, 3.87786017e+01, 6.29693184e+01,
       4.20573445e+01, 3.56613224e+00, 3.24197930e-01, 2.56968675e+01]), array([1.29938438e+00, 7.77712633e+04, 3.57680521e+01, 1.72896122e+02,
       9.57388603e+01, 6.84270319e+00, 4.63284868e+00, 3.50576455e+01]), array([9.37093460e+00, 3.91403629e+04, 3.38642044e+01, 8.45696266e+02,
       5.55658213e+02, 4.60528178e+01, 1.34087800e+01, 6.38019519e+01]), array([2.60168599e+01, 3.97059209e+04, 3.62891299e+01, 2.87970680e+03,
       1.94513388e+03, 6.78003980e+01, 9.94231981e+00, 1.35354306e+02]), array([-1.57170087e+01, -8.29285015e+04,  1.42091330e+02, -1.99381857e+02,
       -2.94052271e+02, -6.41645732e+00,  7.61486321e+00,  1.10201268e+02]), array([2.00805296e+00, 9.51297411e+04, 3.25057935e+01, 1.27088801e+02,
       7.95055216e+01, 9.27197917e+00, 4.1347443

#### Validate filters

In [14]:
predictions = []
for i in range(len(dfs)):
    df_i = dfs[i].drop(['Ticker'], axis='columns')
    # filter our the rows where the 2nd last 'Date' is not '2019-05-01'
    if not find_constant(df_i) \
    and len(df_i) >= 12 \
    and df_i['Adj Close'].mean() < 5000 \
    and df_i.iloc[[-7]].index.date[0] == parse('2019-05-01').date():    
        train_i = df_i[:-6]
        last_date = train_i.iloc[[-1]].index
        # last date in the train should be '2019-05-01' in order to predict next step: '2019-06-01'
        print(last_date.date)   

# print(len(predictions))     # 1325

[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019,

[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019,

[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019,

[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019,

[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019, 5, 1)]
[datetime.date(2019,

#### Get index to obtain corresponding 'Ticker'

In [17]:
idx_list = []          # initialize a list to store index 
ticker_list = []       # initialize a list to store company Ticker

for i in range(len(dfs)):
    df_i = dfs[i].drop(['Ticker'], axis='columns')
    if not find_constant(df_i) \
    and len(df_i) >= 12 \
    and df_i['Adj Close'].mean() < 5000 \
    and df_i.iloc[[-7]].index.date[0] == parse('2019-05-01').date():    
        idx_list.append(i)

for idx in idx_list:
    # store corresponding tickers, to be used later
    ticker_list.append(dfs[idx].Ticker.unique().item())   

# len(ticker_list)  # confirm: 1325
ticker_list

['A',
 'AA',
 'AAL',
 'AAN',
 'AAP',
 'AAWW',
 'AB',
 'ABBV',
 'ABC',
 'ABM',
 'ABMD',
 'ABT',
 'ACAD',
 'ACCO',
 'ACHC',
 'ACIA',
 'ACN',
 'ADBE',
 'ADDDF',
 'ADI',
 'ADM',
 'ADP',
 'ADS',
 'ADSK',
 'ADSW',
 'ADT',
 'ADTN',
 'ADUS',
 'AEE',
 'AEIS',
 'AEO',
 'AEP',
 'AES',
 'AFG',
 'AFI',
 'AFL',
 'AGCO',
 'AGIO',
 'AGO',
 'AGR',
 'AGYS',
 'AIMC',
 'AIN',
 'AIR',
 'AIT',
 'AIZ',
 'AJRD',
 'AKAM',
 'AKBA',
 'ALB',
 'ALG',
 'ALGN',
 'ALGT',
 'ALL',
 'ALLE',
 'ALLY',
 'ALRM',
 'ALRS',
 'ALSN',
 'ALTR',
 'ALXN',
 'AMAG',
 'AMAT',
 'AMD',
 'AME',
 'AMED',
 'AMGN',
 'AMH',
 'AMNB',
 'AMP',
 'AMRC',
 'AMRS',
 'AMSF',
 'AMT',
 'AMTD',
 'AMWD',
 'AMZN',
 'AN',
 'ANAT',
 'ANDE',
 'ANF',
 'ANGO',
 'ANIK',
 'ANSS',
 'ANTM',
 'AON',
 'AOS',
 'APA',
 'APD',
 'APEI',
 'APO',
 'APPF',
 'APPN',
 'APRN',
 'AQMS',
 'ARA',
 'ARAY',
 'ARC',
 'ARCB',
 'ARMK',
 'AROC',
 'ARW',
 'ASB',
 'ASH',
 'ASNA',
 'ASUR',
 'ATEN',
 'ATGE',
 'ATKR',
 'ATNI',
 'ATNX',
 'ATO',
 'ATRA',
 'ATRC',
 'ATRO',
 'ATUS',
 'AVA',
 

### Predict 6 months data '2019-06-01', '2019-07-01', '2019-08-01', '2019-09-01', '2019-10-01', '2019-11-01'

In [18]:
with_predicted = []

for i in range(len(dfs)):
    df_i = dfs[i].drop(['Ticker'], axis='columns')
    if not find_constant(df_i) \
    and len(df_i) >= 12 \
    and df_i['Adj Close'].mean() < 5000 \
    and df_i.iloc[[-7]].index.date[0] == parse('2019-05-01').date():    
        train_i = df_i[:-6]
        store_i = df_i[:-6]

        for mon in range(6):
            model = VAR(endog=train_i)
            model_fit = model.fit()
            prediction = model_fit.forecast(model_fit.y, steps=1)    

            # add prediction of 'next month' to the train set
            if mon == 0:
                store_i.loc['2019-06-01 predict'] = prediction[0]      # store predicted Pstock on '2019-08-01'
                # add actual job-data on '2019-06-01' & Pstock on '2019-08-01' to the training                       
                train_i = df_i[:-5]           
                store_i.loc['2019-06-01 actual'] = df_i[:-5].iloc[-1]  # store actual Pstock on '2019-08-01'
            elif mon == 1:
                store_i.loc['2019-07-01 predict'] = prediction[0]      # store predicted Pstock on '2019-09-01'
                # add actual job-data on '2019-07-01' & Pstock on '2019-09-01' to the training                       
                train_i = df_i[:-4]               
                store_i.loc['2019-07-01 actual'] = df_i[:-4].iloc[-1]  # store actual Pstock on '2019-09-01'
            elif mon == 2:
                store_i.loc['2019-08-01 predict'] = prediction[0]      # store predicted Pstock on '2019-10-01'
                # add actual job-data on '2019-08-01' & Pstock on '2019-10-01' to the training                       
                train_i = df_i[:-3]          
                store_i.loc['2019-08-01 actual'] = df_i[:-3].iloc[-1]  # store actual Pstock on '2019-10-01'
            elif mon == 3:
                store_i.loc['2019-09-01 predict'] = prediction[0]      # store predicted Pstock on '2019-11-01'
                # add actual job-data on '2019-09-01' & Pstock on '2019-11-01' to the training                       
                train_i = df_i[:-2]                   
                store_i.loc['2019-09-01 actual'] = df_i[:-2].iloc[-1]  # store actual Pstock on '2019-11-01'
            elif mon == 4:
                store_i.loc['2019-10-01 predict'] = prediction[0]      # store predicted Pstock on '2019-12-01'
                # add actual job-data on '2019-10-01' & Pstock on '2019-12-01' to the training                       
                train_i = df_i[:-1]            
                store_i.loc['2019-10-01 actual'] = df_i[:-1].iloc[-1]  # store actual Pstock on '2019-12-01'
            elif mon == 5:   
                store_i.loc['2019-11-01 predict'] = prediction[0]      # store predicted Pstock on '2020-01-01'
                # add actual job-data on '2019-11-01' & Pstock on '2020-01-01' to the training                       
                train_i = df_i[:]           
                store_i.loc['2019-11-01 actual'] = df_i[:].iloc[-1]    # store actual Pstock on '2020-01-01'
                
        #store only the predicted months and one month before (last 13 rows) to calculate return
        with_predicted.append(store_i[-13: ])   

In [19]:
# check: everything works correctly
with_predicted[0]  # first company's information

New_Cbsa        Salary  average_posting_duration  \
Date                                                                    
2019-05-01 00:00:00  2.000000  91467.278689                 31.618421   
2019-06-01 predict  -0.133181  90288.997115                 38.172600   
2019-06-01 actual    0.000000  82737.600000                 35.919463   
2019-07-01 predict   1.199409  86460.418491                 38.308635   
2019-07-01 actual    2.000000  72342.105263                 47.119048   
2019-08-01 predict   1.706587  82600.050879                 33.691043   
2019-08-01 actual    1.000000  74112.007463                 61.954545   
2019-09-01 predict  -1.021609  70627.785002                 27.891132   
2019-09-01 actual    1.000000  72236.660714                 38.642857   
2019-10-01 predict   1.399041  77916.160088                 29.464798   
2019-10-01 actual    1.000000  72301.926829                 17.900000   
2019-11-01 predict   0.189537  75635.756971                 20.702036   
2019-11-01 actual    1.000000  72277.847222                 30.210938   

                     Job_posting  new_posting  impCount  intCount  Adj Close  
Date                                                                          
2019-05-01 00:00:00   152.000000   100.000000  1.000000  2.000000  68.671310  
2019-06-01 predict    122.626647    75.477750  0.206099  2.390266  71.166221  
2019-06-01 actual     149.000000    98.000000  3.000000  4.000000  70.353226  
2019-07-01 predict    127.966312    75.281774  2.017741  5.812250  71.719231  
2019-07-01 actual      84.000000    83.000000  1.000000  4.000000  75.977585  
2019-08-01 predict     71.364039    64.112010  3.064415  7.047530  75.226026  
2019-08-01 actual      22.000000   155.000000  0.000000  3.000000  75.105080  
2019-09-01 predict    -28.406927   173.159345  3.964441  2.382174  79.217287  
2019-09-01 actual      14.000000    84.000000  0.000000  3.000000  80.082336  
2019-10-01 predict     12.851021    79.996121  1.555970  4.222731  78.452564  
2019-10-01 actual      70.000000   144.000000  2.000000  4.000000  84.762299  
2019-11-01 predict     50.264372   108.721658  3.753409  5.412055  85.901143  
2019-11-01 actual     128.000000    81.000000  3.000000  6.000000  83.838264

**Note**: The rows that ends with `'actual'` are only stored here to provide the actual `'Adj Close'` price for that month, we don't need to look at the other rows here. These rows will be dropped eventually.

### Add company ticker back

In [20]:
# check: make sure the lists have the same length
print(len(ticker_list))
print(len(with_predicted))

1325
1325


In [23]:
for i in range(len(with_predicted)):
    # for each predicted df, append a column of its corresponding company ticker
    with_predicted[i]['Ticker'] = ticker_list[i]  
    
with_predicted

[                     New_Cbsa        Salary  average_posting_duration  \
 Date                                                                    
 2019-05-01 00:00:00  2.000000  91467.278689                 31.618421   
 2019-06-01 predict  -0.133181  90288.997115                 38.172600   
 2019-06-01 actual    0.000000  82737.600000                 35.919463   
 2019-07-01 predict   1.199409  86460.418491                 38.308635   
 2019-07-01 actual    2.000000  72342.105263                 47.119048   
 2019-08-01 predict   1.706587  82600.050879                 33.691043   
 2019-08-01 actual    1.000000  74112.007463                 61.954545   
 2019-09-01 predict  -1.021609  70627.785002                 27.891132   
 2019-09-01 actual    1.000000  72236.660714                 38.642857   
 2019-10-01 predict   1.399041  77916.160088                 29.464798   
 2019-10-01 actual    1.000000  72301.926829                 17.900000   
 2019-11-01 predict   0.189537  75635.

In [22]:
# check a random df in the list: make sure everything works correctly
with_predicted[25]

New_Cbsa        Salary  average_posting_duration  \
Date                                                                     
2019-05-01 00:00:00   3.000000  55010.363764                 33.461631   
2019-06-01 predict    1.219525  55608.252180                 36.630830   
2019-06-01 actual    22.000000  55048.992674                 34.932377   
2019-07-01 predict   23.305477  58411.908872                  0.242809   
2019-07-01 actual    16.000000  52631.012022                 42.410134   
2019-08-01 predict   18.641276  57203.408688                 26.977808   
2019-08-01 actual     3.000000  54708.026119                 47.326478   
2019-09-01 predict   -1.060545  58580.668380                 29.146051   
2019-09-01 actual     2.000000  54647.916667                 34.590909   
2019-10-01 predict   10.470085  53059.604819                 12.018829   
2019-10-01 actual     5.000000  53374.816176                 16.687898   
2019-11-01 predict    7.937190  53413.165416                 13.210274   
2019-11-01 actual     3.000000  56182.368421                 24.965478   

                     Job_posting  new_posting    impCount   intCount  \
Date                                                                   
2019-05-01 00:00:00  1668.000000   949.000000   57.000000  24.000000   
2019-06-01 predict   1575.968973   801.286597   40.841625  32.822771   
2019-06-01 actual    1464.000000   969.000000   43.000000  27.000000   
2019-07-01 predict   2398.869762  1874.650624  104.637588  37.212795   
2019-07-01 actual    1046.000000  1110.000000   41.000000  22.000000   
2019-08-01 predict   1337.825055  1357.585950   64.063887  18.998239   
2019-08-01 actual     389.000000  1530.000000   39.000000  14.000000   
2019-09-01 predict    389.996387  1428.188187   55.992943   9.644912   
2019-09-01 actual     110.000000   807.000000   45.000000  14.000000   
2019-10-01 predict   1017.413869  1352.256473   46.220383  29.331632   
2019-10-01 actual     471.000000  1003.000000   61.000000  20.000000   
2019-11-01 predict    726.393989  1109.116713   41.283827  25.679925   
2019-11-01 actual     869.000000   613.000000   72.000000  20.000000   

                     Adj Close Ticker  
Date                                   
2019-05-01 00:00:00   5.713102    ADT  
2019-06-01 predict    7.172638    ADT  
2019-06-01 actual     4.282578    ADT  
2019-07-01 predict    7.068175    ADT  
2019-07-01 actual     5.676041    ADT  
2019-08-01 predict    5.562544    ADT  
2019-08-01 actual     7.006787    ADT  
2019-09-01 predict    5.065620    ADT  
2019-09-01 actual     8.364691    ADT  
2019-10-01 predict    6.498387    ADT  
2019-10-01 actual     7.803586    ADT  
2019-11-01 predict    7.137594    ADT  
2019-11-01 actual     6.258614    ADT

### Combine Table

In [24]:
combine_df = pd.concat([i.iloc[:,-2:] for i in with_predicted]).reset_index()
combine_df.head(15) 

Date  Adj Close Ticker
0   2019-05-01 00:00:00  68.671310      A
1    2019-06-01 predict  71.166221      A
2     2019-06-01 actual  70.353226      A
3    2019-07-01 predict  71.719231      A
4     2019-07-01 actual  75.977585      A
5    2019-08-01 predict  75.226026      A
6     2019-08-01 actual  75.105080      A
7    2019-09-01 predict  79.217287      A
8     2019-09-01 actual  80.082336      A
9    2019-10-01 predict  78.452564      A
10    2019-10-01 actual  84.762299      A
11   2019-11-01 predict  85.901143      A
12    2019-11-01 actual  83.838264      A
13  2019-05-01 00:00:00  22.490000     AA
14   2019-06-01 predict  25.696867     AA

**Note**: each company has 13 rows (2 rows for each of the 6 months (actual & predicted) & 1 row for Pstock on '2019-05-05')

### Add 'Return' column

In [25]:
# shift 1 to get correponding actual close price (will only be valid for the 'predict' rows)
combine_df['Act Prev Close'] = combine_df.groupby(['Ticker'])['Adj Close'].shift(1)
combine_df.head(15)

Date  Adj Close Ticker  Act Prev Close
0   2019-05-01 00:00:00  68.671310      A             NaN
1    2019-06-01 predict  71.166221      A       68.671310
2     2019-06-01 actual  70.353226      A       71.166221
3    2019-07-01 predict  71.719231      A       70.353226
4     2019-07-01 actual  75.977585      A       71.719231
5    2019-08-01 predict  75.226026      A       75.977585
6     2019-08-01 actual  75.105080      A       75.226026
7    2019-09-01 predict  79.217287      A       75.105080
8     2019-09-01 actual  80.082336      A       79.217287
9    2019-10-01 predict  78.452564      A       80.082336
10    2019-10-01 actual  84.762299      A       78.452564
11   2019-11-01 predict  85.901143      A       84.762299
12    2019-11-01 actual  83.838264      A       85.901143
13  2019-05-01 00:00:00  22.490000     AA             NaN
14   2019-06-01 predict  25.696867     AA       22.490000

**Note**: The rows ending with 'actual' will be dropped later. They are here to serve as the reference of the actual stock price.

In [30]:
# calculate monthly return
combine_df['Return'] = 100 * (combine_df['Adj Close'] - combine_df['Act Prev Close']) / combine_df['Act Prev Close']
combine_df.head(15)

Date  Adj Close Ticker  Act Prev Close     Return
0   2019-05-01 00:00:00  68.671310      A             NaN        NaN
1    2019-06-01 predict  71.166221      A       68.671310   3.633120
2     2019-06-01 actual  70.353226      A       71.166221  -1.142390
3    2019-07-01 predict  71.719231      A       70.353226   1.941639
4     2019-07-01 actual  75.977585      A       71.719231   5.937534
5    2019-08-01 predict  75.226026      A       75.977585  -0.989184
6     2019-08-01 actual  75.105080      A       75.226026  -0.160778
7    2019-09-01 predict  79.217287      A       75.105080   5.475272
8     2019-09-01 actual  80.082336      A       79.217287   1.091996
9    2019-10-01 predict  78.452564      A       80.082336  -2.035121
10    2019-10-01 actual  84.762299      A       78.452564   8.042738
11   2019-11-01 predict  85.901143      A       84.762299   1.343574
12    2019-11-01 actual  83.838264      A       85.901143  -2.401456
13  2019-05-01 00:00:00  22.490000     AA             NaN        NaN
14   2019-06-01 predict  25.696867     AA       22.490000  14.259083

In [31]:
# remove unnecessary rows of each ticker

# Remove the '2019-05-1' observation from each company
new_df = combine_df.dropna()     

# remove the rows ending with 'actual'
new_df = new_df[new_df.Date != '2019-06-01 actual']
new_df = new_df[new_df.Date != '2019-07-01 actual']
new_df = new_df[new_df.Date != '2019-08-01 actual']
new_df = new_df[new_df.Date != '2019-09-01 actual']
new_df = new_df[new_df.Date != '2019-10-01 actual']
new_df = new_df[new_df.Date != '2019-11-01 actual']

new_df   # results: 7950 rows  (confirm: 7950/6 = 1325 tickers)

Date  Adj Close Ticker  Act Prev Close     Return
1      2019-06-01 predict  71.166221      A       68.671310   3.633120
3      2019-07-01 predict  71.719231      A       70.353226   1.941639
5      2019-08-01 predict  75.226026      A       75.977585  -0.989184
7      2019-09-01 predict  79.217287      A       75.105080   5.475272
9      2019-10-01 predict  78.452564      A       80.082336  -2.035121
...                   ...        ...    ...             ...        ...
17215  2019-07-01 predict  24.192164   ZUMZ       25.980000  -6.881586
17217  2019-08-01 predict  27.662573   ZUMZ       31.680000 -12.681273
17219  2019-09-01 predict  28.147064   ZUMZ       31.910000 -11.792342
17221  2019-10-01 predict  27.601361   ZUMZ       29.540001  -6.562762
17223  2019-11-01 predict  33.570202   ZUMZ       34.540001  -2.807756

[7950 rows x 5 columns]

In [32]:
# remove unnecessary columns of each ticker to have only Date, Company Ticker, and Stock Return
new_df = new_df[['Date', 'Ticker', 'Return']]
new_df

Date Ticker     Return
1      2019-06-01 predict      A   3.633120
3      2019-07-01 predict      A   1.941639
5      2019-08-01 predict      A  -0.989184
7      2019-09-01 predict      A   5.475272
9      2019-10-01 predict      A  -2.035121
...                   ...    ...        ...
17215  2019-07-01 predict   ZUMZ  -6.881586
17217  2019-08-01 predict   ZUMZ -12.681273
17219  2019-09-01 predict   ZUMZ -11.792342
17221  2019-10-01 predict   ZUMZ  -6.562762
17223  2019-11-01 predict   ZUMZ  -2.807756

[7950 rows x 3 columns]

### Reformat Table

- to be better suited for usage in the stock picking simulation

In [33]:
reformat_df = new_df.pivot(columns = 'Date', values = 'Return', index = 'Ticker')
reformat_df.columns = ['2019-08', '2019-09', '2019-10', '2019-11', '2019-12', '2020-01']
reformat_df.reset_index()
reformat_df

2019-08    2019-09    2019-10    2019-11    2019-12    2020-01
Ticker                                                                  
A        3.633120   1.941639  -0.989184   5.475272  -2.035121   1.343574
AA      14.259083  -1.763753   6.228646   6.482264  -0.420609   0.550378
AAL     16.110883   1.934161  -2.993551 -31.895237   7.919258  10.497010
AAN      1.698000   6.734586   1.934730  36.191153 -18.230439  -3.851623
AAP     -9.364314  -6.389783 -19.404428  38.331948   7.888393  12.771770
...           ...        ...        ...        ...        ...        ...
ZGNX     2.006088 -15.245307  10.392096  21.964742   1.974457   0.896183
ZION     0.560555  -7.599444  -4.146234   2.135531   8.367711   5.627621
ZNGA    -7.435770  13.148979  10.374427   2.200228   2.926059  -8.774518
ZTS      2.940268   2.485700   4.705163   4.650009   5.501232   0.829577
ZUMZ    -4.981741  -6.881586 -12.681273 -11.792342  -6.562762  -2.807756

[1325 rows x 6 columns]

### Export Output in a  File

In [34]:
reformat_df.to_csv('VAR_Pedicted_Returns.csv')